# Handwritten Recognition

## Initialization

### Imports

In [33]:
import os
import numpy as np

import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

from build_db import build_db
from data_augmentation import data_augmentation
from labelisation import labelize_data
from utils.extract_features import features_extraction

### Global variables

In [34]:
# all the variable related to the path.
# to read the csv for example.

# path of the current folder.
SCRIPT_DIR = os.getcwd()
# path of the parent folder.
PARENT_DIR = os.path.dirname(SCRIPT_DIR)
DATA_FOLDER = os.path.join(PARENT_DIR,  'data')
CSV_LABEL_PATH = os.path.join(DATA_FOLDER, "labels.csv")
MATRIX_FOLDER = os.path.join(DATA_FOLDER, "matrix")
RESULT_FOLDER = os.path.join(DATA_FOLDER, "results")

## Part I : DB build 

In [6]:
# Create the DB from the raw data
# remove the actuals files in the DB.
# create new DB content from the raw data.
build_db()

Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/b removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/c removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/d removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/e removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/f removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/g removed succefully
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/h removed succefully


KeyboardInterrupt: 

**Note :** Clean the database manually can be useful. Especially to remove bad data, and have a clean database of handwritten letters.

### DB augmentation

In [ ]:
# DB augmentation
# augment the DB size using rotation, blur and other transformations on current images.
data_augmentation()
# store the data information into a csv file : useful for sampling 
labelize_data()

Début de l'augmentation des données...
Augmentation done for letter : a
Augmentation done for letter : b
Augmentation done for letter : c
Augmentation done for letter : d
Augmentation done for letter : e
Augmentation done for letter : f
Augmentation done for letter : g
Augmentation done for letter : h
Augmentation done for letter : i
Augmentation done for letter : j
Augmentation done for letter : k
Augmentation done for letter : l
Augmentation done for letter : m
Augmentation done for letter : n
Augmentation done for letter : o
Augmentation done for letter : p
Augmentation done for letter : q
Augmentation done for letter : r
Augmentation done for letter : s
Augmentation done for letter : t
Augmentation done for letter : u
Augmentation done for letter : v
Augmentation done for letter : w
Augmentation done for letter : x
Augmentation done for letter : y
Augmentation done for letter : z
Terminé ! Chaque lettre a maintenant environ 498 exemples.
CSV created


## Part II : Features extraction

In [35]:
# read the csv file
data_filepath = pd.read_csv(CSV_LABEL_PATH)

### Features extraction

In [ ]:
# choose the method of features extraction and apply it.
methods = ["HOG", "HU", "GEOMETRIC"]

for method in methods:
    features_extraction(df_labels=data_filepath, method=method)


The df is complete (data + labels) : True
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_100.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_100_aug_0.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_100_aug_1.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_100_aug_2.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_100_aug_3.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_100_aug_4.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_101.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\characters/a\char_101_aug_0.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handw

## Part III : Classifier preparation

### Model choice and training

In [42]:
## Imports 
# classifiers
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC

# Utils
from sklearn.model_selection import StratifiedKFold, cross_val_score, cross_val_predict
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay, classification_report

**Utils**

In [43]:
# --------------------------------------------------
# Stratified cross-validation
# --------------------------------------------------
cv = StratifiedKFold(
    n_splits=5,
    shuffle=True,
    random_state=42
)


SCALER = StandardScaler()

# Cross-validated accuracy
def cross_validation_report(classifier, classifier_name, method, X_train, y_train, y_test, y_pred):
    cv_scores = cross_val_score(classifier, X_train, y_train, cv=cv)

    # save the results
    with open (f"{RESULT_FOLDER}/cv_report_{classifier_name}_{method}.txt", "w") as f:
        f.write("Cross-validated accuracy scores: " + str(cv_scores) + "\n")
        f.write("Mean accuracy: " + str(np.mean(cv_scores)) + "\n\n")
        f.write("Classification report (CV):\n")
        f.write(classification_report(y_test, y_pred))


# To plot the confusion matrix
def confusion_matrix_construction(classifier_name, method, y_pred, y_test):
    cm = confusion_matrix(y_test, y_pred)
    disp = ConfusionMatrixDisplay(confusion_matrix=cm, display_labels=np.unique(y_test))
    disp.plot(cmap=plt.cm.Blues, values_format='d')
    plt.title(f"Matrice de confusion - {classifier_name} - {method}")
    plt.savefig(f"{MATRIX_FOLDER}/matrix_{classifier_name}_{method}.png", dpi=300, bbox_inches='tight')  # Save in PNG

#### Random Forest

In [44]:
# --------------------------------------------------
# Random Forest classifier
# --------------------------------------------------
rf_clf = RandomForestClassifier(
    n_estimators=300,
    max_depth=10,
    min_samples_leaf=2,
    class_weight="balanced",
    random_state=42
)

#### KNN

In [45]:
# --------------------------------------------------
# k-NN classifier
# --------------------------------------------------
knn_clf = KNeighborsClassifier(
    n_neighbors=3,        # small value for small dataset
    metric='euclidean',   # standard distance
    weights='distance'    # closer neighbors matter more
)

#### SVM

In [46]:
# --------------------------------------------------
# SVM classifier
# --------------------------------------------------
svm_clf = SVC(
    kernel='rbf', 
    C=1.0, 
    gamma='scale')  # Base parameters

## PART IV : Main loop - Classifier evaluation

In [ ]:
def model_evaluation(method):
    print(f"--- Evaluation for method: {method} ---")

    ### Data loading
    DATA_DIR = os.path.join(DATA_FOLDER, "features", method)
    X = np.load(os.path.join(DATA_DIR, f"features_{method}.npy"))
    y = np.load(os.path.join(DATA_DIR, f"labels_{method}.npy"), allow_pickle=True)


    ### Normalisation
    X_scaled = SCALER.fit_transform(X)


    ### Sampling
    X_train, X_test, y_train, y_test = train_test_split(
        X_scaled, y, test_size=0.2, random_state=42, stratify=y
    )


    ### Evaluation
    classifiers = {
        "Random Forest": rf_clf,
        "k-NN": knn_clf,
        "SVM": svm_clf
    }

    for name, clf in classifiers.items():
        print(f"Evaluating {name} classifier with {method} features.")
        # Train the model on the entire training set
        clf.fit(X_train, y_train)

        # Predict on the test set
        y_pred = clf.predict(X_test)

        # Save results for evaluation        
        cross_validation_report(classifier=clf, classifier_name=name, method=method, X_train=X_train, y_train=y_train, y_test=y_test, y_pred=y_pred)
        confusion_matrix_construction(classifier_name=name, method=method, y_pred=y_pred, y_test=y_test)

In [ ]:
for method in methods:
    model_evaluation(method=method)

### Model Choice


**Mean accuracy** table : 

|       |   HOG   |   HU    |GEOMETRIC| Eighteen |
|:------|:-------:|:-------:|:-------:|:--------:|
|**RF** |0.934    |0.238    |0.520    |0.536     |
|**KNN**|0.980    |0.192    |0.489    |0.482     | 
|**SVM**|0.982    |0.222    |0.541    |0.550     |

Based on the previous table, the best method of features extraction is, without any doubt, the HOG method.

Regarding the model choice, Random Forest is less efficient than other models. The two other models have approximately the same efficacy, based on the mean accuracy table and the confusion matrix.

## Part V : Model application

### Intialization

In [47]:
# Optional : re-train the best model on the entire dataset and predict new data
# Here we assume SVM with HOG features is the best model
method = "HOG"
DATA_DIR = os.path.join(DATA_FOLDER, "features", method)
X = np.load(os.path.join(DATA_DIR, f"features_{method}.npy"))
y = np.load(os.path.join(DATA_DIR, f"labels_{method}.npy"), allow_pickle=True)

X_scaled = SCALER.fit_transform(X)

### Training of the model

In [48]:
svm_clf.fit(X, y)

SVC()

In [49]:
knn_clf.fit(X, y)

KNeighborsClassifier(metric='euclidean', n_neighbors=3, weights='distance')

In [52]:
rf_clf.fit(X, y)

RandomForestClassifier(class_weight='balanced', max_depth=10,
                       min_samples_leaf=2, n_estimators=300, random_state=42)

### Main function

In [53]:
from new_data_preparation import prepare_new_data
from glob import glob

words_files = glob(os.path.join(DATA_FOLDER, "words", "*.jpg"))

def identify_words(classifier):
    results = []
    for file in words_files:
        file = os.path.basename(file)
        print(f"Processing file: {file}")
        ## The new_data have to follow the same pipeline as the training data
        # The file to process is supposed to be in the right folder : data/words/
        new_data = prepare_new_data(filename=file, features_extraction_method="HOG", prepare_new_data= True)

        # Normalisation
        X_new = SCALER.fit_transform(new_data)

        # Prediction
        predictions = classifier.predict(X_new)
        result = "".join(predictions)
        results.append((file, result))

    return results


results_knn = identify_words(knn_clf)
results_svm = identify_words(svm_clf)
results_rf = identify_words(rf_clf)

Processing file: lancegoat.jpg
Files from c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters removed succefully
This word contains 9 characters.
Extraction finished !

Dataframe created !

The df is complete (data + labels) : False
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters\char_00.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters\char_01.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters\char_02.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters\char_04.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters\char_06.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_handwritten_recognition\data\words\characters\char_07.png
c:\Users\tv68e\Documents\INSA_Lyon\Image_analysis\M1_h

### Results

In [56]:
print("Final results on new data for SVM:")
for file, result in results_svm:
    print(f"File: {file}, Result: {result}")    

print("\n")
print("Final results on new data for KNN:")
for file, result in results_knn:
    print(f"File: {file}, Result: {result}")

print("\n")
print("Final results on new data for Random Forest:")
for file, result in results_rf:
    print(f"File: {file}, Result: {result}")    

Final results on new data for SVM:
File: lancegoat.jpg, Result: fffffffff
File: results.jpg, Result: fffffff
File: xylophone.jpg, Result: fffffffff


Final results on new data for KNN:
File: lancegoat.jpg, Result: lancegoat
File: results.jpg, Result: resalts
File: xylophone.jpg, Result: xglophone


Final results on new data for Random Forest:
File: lancegoat.jpg, Result: famccgoaf
File: results.jpg, Result: rcsadus
File: xylophone.jpg, Result: xyyozhono


Here, the bests results are for the K-NN classifier.

We can suppose that, with a larger volume of data, the efficacy of the results would be better.

Regarding the SVM model, the results are surprising but I don't have any explaination about it.